In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
from pathlib import Path

if "workding_dir" not in locals():
    try:
        from google.colab import drive
        drive.mount('/content/drive')
        workding_dir = "/content/drive/MyDrive/logical-reasoning/"
    except ModuleNotFoundError:
        workding_dir = str(Path.cwd().parent)

In [3]:
import os
import sys

os.chdir(workding_dir)
sys.path.append(workding_dir)
print("workding dir:", workding_dir)

workding dir: d:\code\projects\logical-reasoning


In [4]:
from dotenv import find_dotenv, load_dotenv

found_dotenv = find_dotenv(".env")

if len(found_dotenv) == 0:
    found_dotenv = find_dotenv(".env.example")
print(f"loading env vars from: {found_dotenv}")
load_dotenv(found_dotenv, override=True)

loading env vars from: d:\code\projects\logical-reasoning\.env


True

In [5]:
import os

model_name = os.getenv("MODEL_NAME")
data_path = os.getenv("LOGICAL_REASONING_DATA_PATH")
results_path = os.getenv("LOGICAL_REASONING_RESULTS_PATH")
max_new_tokens = int(os.getenv("MAX_NEW_TOKENS", 2048))

print(model_name, data_path, results_path, max_new_tokens)

claude-3-5-sonnet-20240620 datasets/mgtv data/openai_results.csv 16


In [6]:
from llm_toolkit.logical_reasoning_utils import *

loading d:\code\projects\logical-reasoning\llm_toolkit\logical_reasoning_utils.py


In [7]:
df = pd.read_csv(results_path)

In [8]:
from llm_toolkit.llm_utils import print_row_details

best_run = "gpt-4o/shots-10"
invalid_rows = df["重要" == df[best_run]]
print_row_details(invalid_rows)

--------------------------------------------------
text: 哭的人和死者的关系重要吗 
--------------------------------------------------
label: 是
--------------------------------------------------
title: 甄庄哭声
--------------------------------------------------
puzzle: 在一个安静的夜晚，小村庄的湖边突然传来了阵阵哭泣声。第二天早晨，村长甄锐发现湖边的石头上放着一顶破旧的帽子，但没有人知道这顶帽子是从哪里来的，哭泣声又是为何。请还原故事真相。
--------------------------------------------------
truth: 原来，这顶破旧的帽子属于一个小男孩，他小时候与爷爷在湖边生活。爷爷教他钓鱼、游泳，还告诉他湖中的海龟是他们的朋友。后来，小男孩随父母去了城市生活，但每年夏天都会回到村子探望爷爷。然而，去年夏天，爷爷因病去世，小男孩伤心欲绝。今年夏天，他回到村子，来到湖边，想起和爷爷的美好回忆，忍不住哭泣。他将爷爷的帽子放在湖边的石头上，希望能让爷爷的在天之灵得到安慰。那晚的哭泣声正是小男孩在祭莫他亲爱的爷爷。
--------------------------------------------------
gpt-4o-mini/shots-00: 不重要
--------------------------------------------------
gpt-4o-mini/shots-05: 不重要
--------------------------------------------------
gpt-4o-mini/shots-10: 不重要
--------------------------------------------------
gpt-4o-mini/shots-20: 不重要
--------------------------------------------------
gpt-4o-mini/shots-30: 不重要
-----------------

In [7]:
datasets = load_logical_reasoning_dataset(data_path)

prompt = get_few_shot_prompt_template(10, datasets["train"].to_pandas(), debug=True)

loading train/test data files
DatasetDict({
    train: Dataset({
        features: ['text', 'label', 'answer', 'title', 'puzzle', 'truth'],
        num_rows: 25000
    })
    test: Dataset({
        features: ['text', 'label', 'answer', 'title', 'puzzle', 'truth'],
        num_rows: 3000
    })
})
num_shots: 10
labels: ['不是' '不重要' '是' '问法错误' '回答正确']
P2_few_shot: 你是一个情景猜谜游戏的主持人。游戏规则如下：

1. 参与者会得到一个谜面，谜面会描述一个简单又难以理解的事件。
2. 主持人知道谜底，谜底是谜面的答案。
3. 参与者可以询问任何封闭式问题来找寻事件的真相。
4. 对于每个问题，主持人将根据实际情况回答以下五个选项之一：是、不是、不重要、回答正确、问法错误。各回答的判断标准如下：
   - 若谜面和谜底能找到问题的答案，回答：是或者不是
   - 若谜面和谜底不能直接或者间接推断出问题的答案，回答：不重要
   - 若参与者提问不是一个封闭式问题或者问题难以理解，回答：问法错误
   - 若参与者提问基本还原了谜底真相，回答：回答正确
5. 回答中不能添加任何其它信息，也不能省略选项中的任何一个字。例如，不可以把“不是”省略成“不”。

请严格按照这些规则回答参与者提出的问题。

示例输入和输出: 
谜面: 在甄家村里，有一个古老的传说：每年南瓜丰收的季节，南瓜田里总有一个最大的南瓜会不翼而飞，村民们对此现象困惑不解。请找出南瓜失踪背后的原因。
谜底: 真相原来与一位年迈的农夫有关。这位农夫年轻时，曾与一位美丽的姑娘相恋。他们约定在南瓜丰收的季节结婚。然而，命运弄人，姑娘在婚礼前的一场意外中离世。悲伤的农夫为了纪念心爱的姑娘，每年都会将最大的南瓜偷走，放到姑娘的墓前，以此寄托自己的哀思。这一行为延续了多年，成为了乡村里一个神秘的传说。
参与者提出的问题: 偷的人信神吗
回答: 不是

谜面: 在甄家

In [10]:
row = invalid_rows.iloc[0]
print(prompt.format(row["puzzle"], row["truth"], row["text"]))

你是一个情景猜谜游戏的主持人。游戏规则如下：

1. 参与者会得到一个谜面，谜面会描述一个简单又难以理解的事件。
2. 主持人知道谜底，谜底是谜面的答案。
3. 参与者可以询问任何封闭式问题来找寻事件的真相。
4. 对于每个问题，主持人将根据实际情况回答以下五个选项之一：是、不是、不重要、回答正确、问法错误。各回答的判断标准如下：
   - 若谜面和谜底能找到问题的答案，回答：是或者不是
   - 若谜面和谜底不能直接或者间接推断出问题的答案，回答：不重要
   - 若参与者提问不是一个封闭式问题或者问题难以理解，回答：问法错误
   - 若参与者提问基本还原了谜底真相，回答：回答正确
5. 回答中不能添加任何其它信息，也不能省略选项中的任何一个字。例如，不可以把“不是”省略成“不”。

请严格按照这些规则回答参与者提出的问题。

示例输入和输出: 
谜面: 在甄家村里，有一个古老的传说：每年南瓜丰收的季节，南瓜田里总有一个最大的南瓜会不翼而飞，村民们对此现象困惑不解。请找出南瓜失踪背后的原因。
谜底: 真相原来与一位年迈的农夫有关。这位农夫年轻时，曾与一位美丽的姑娘相恋。他们约定在南瓜丰收的季节结婚。然而，命运弄人，姑娘在婚礼前的一场意外中离世。悲伤的农夫为了纪念心爱的姑娘，每年都会将最大的南瓜偷走，放到姑娘的墓前，以此寄托自己的哀思。这一行为延续了多年，成为了乡村里一个神秘的传说。
参与者提出的问题: 偷的人信神吗
回答: 不是

谜面: 在甄家村里，有一个古老的传说：每年南瓜丰收的季节，南瓜田里总有一个最大的南瓜会不翼而飞，村民们对此现象困惑不解。请找出南瓜失踪背后的原因。
谜底: 真相原来与一位年迈的农夫有关。这位农夫年轻时，曾与一位美丽的姑娘相恋。他们约定在南瓜丰收的季节结婚。然而，命运弄人，姑娘在婚礼前的一场意外中离世。悲伤的农夫为了纪念心爱的姑娘，每年都会将最大的南瓜偷走，放到姑娘的墓前，以此寄托自己的哀思。这一行为延续了多年，成为了乡村里一个神秘的传说。
参与者提出的问题: 村庄里的人喜欢南瓜嘛
回答: 不重要

谜面: 在甄家村里，有一个古老的传说：每年南瓜丰收的季节，南瓜田里总有一个最大的南瓜会不翼而飞，村民们对此现象困惑不解。请找出南瓜失踪背后的原因。
谜底: 真相原来与一位年迈的农夫有关。这位农夫年轻时，曾与一位美丽的姑娘相恋。他们约定在南瓜

In [11]:
%%time

reasoning_with_openai(row, prompt, max_tokens=max_new_tokens, model="gpt-4o")

CPU times: total: 141 ms
Wall time: 1.63 s


'是'

In [12]:
%%time

reasoning_with_openai(row, prompt, max_tokens=max_new_tokens, model="gpt-4o", temperature=1)

CPU times: total: 78.1 ms
Wall time: 970 ms


'是'

In [37]:
%%time

reasoning_with_openai(row, prompt, max_tokens=max_new_tokens, model="gpt-4o-mini")

CPU times: total: 15.6 ms
Wall time: 1.38 s


'不重要'

In [38]:
%%time

reasoning_with_openai(
    row, prompt, max_tokens=max_new_tokens, model="gpt-4o-mini", temperature=1
)

CPU times: total: 78.1 ms
Wall time: 968 ms


'不重要'

In [39]:
%%time

reasoning_with_openai(
    row,
    prompt,
    max_tokens=None,
    model="o1-preview",
    temperature=1,
    using_system_prompt=False,
)

CPU times: total: 31.2 ms
Wall time: 12.2 s


'是'

In [40]:
%%time

reasoning_with_openai(
    row,
    prompt,
    max_tokens=None,
    model="o1-mini",
    temperature=1,
    using_system_prompt=False,
)

CPU times: total: 78.1 ms
Wall time: 3.96 s


'是'

## Run Batch Inference

In [18]:
df_batch = load_openai_batch_data(data_path)

loading existing data from: datasets/mgtv/o1-mini.jsonl


In [19]:
from llm_toolkit.llm_utils import print_row_details

print_row_details(df_batch)

--------------------------------------------------
custom_id: request-1
--------------------------------------------------
method: POST
--------------------------------------------------
url: /v1/chat/completions
--------------------------------------------------
body: {'model': 'o1-mini', 'messages': [{'role': 'user', 'content': '你是一个情景猜谜游戏的主持人。游戏规则如下：\n\n1. 参与者会得到一个谜面，谜面会描述一个简单又难以理解的事件。\n2. 主持人知道谜底，谜底是谜面的答案。\n3. 参与者可以询问任何封闭式问题来找寻事件的真相。\n4. 对于每个问题，主持人将根据实际情况回答以下五个选项之一：是、不是、不重要、回答正确、问法错误。各回答的判断标准如下：\n   - 若谜面和谜底能找到问题的答案，回答：是或者不是\n   - 若谜面和谜底不能直接或者间接推断出问题的答案，回答：不重要\n   - 若参与者提问不是一个封闭式问题或者问题难以理解，回答：问法错误\n   - 若参与者提问基本还原了谜底真相，回答：回答正确\n5. 回答中不能添加任何其它信息，也不能省略选项中的任何一个字。例如，不可以把“不是”省略成“不”。\n\n请严格按照这些规则回答参与者提出的问题。\n\n示例输入和输出: \n谜面: 在甄家村里，有一个古老的传说：每年南瓜丰收的季节，南瓜田里总有一个最大的南瓜会不翼而飞，村民们对此现象困惑不解。请找出南瓜失踪背后的原因。\n谜底: 真相原来与一位年迈的农夫有关。这位农夫年轻时，曾与一位美丽的姑娘相恋。他们约定在南瓜丰收的季节结婚。然而，命运弄人，姑娘在婚礼前的一场意外中离世。悲伤的农夫为了纪念心爱的姑娘，每年都会将最大的南瓜偷走，放到姑娘的墓前，以此寄托自己的哀思。这一行为延续了多年，成为了乡村里一个神秘的传说。\n参与者提出的问题: 偷的人信神吗\n回答: 不是\n\n谜面: 在甄家村里，有一个古老的传说：

In [20]:
from openai import OpenAI

client = OpenAI()

batch_input_file = client.files.create(
    file=open("datasets/mgtv/o1-mini.jsonl", "rb"), purpose="batch"
)

In [21]:
batch_input_file

FileObject(id='file-HfMbJ2tKqWAwYvlW3nYtdhIO', bytes=57923228, created_at=1726233393, filename='o1-mini.jsonl', object='file', purpose='batch', status='processed', status_details=None)

In [22]:
batch_input_file_id = batch_input_file.id

client.batches.create(
    input_file_id=batch_input_file_id,
    endpoint="/v1/chat/completions",
    completion_window="24h",
    metadata={
      "description": "nightly eval job - o1-mini",
    }
)

Batch(id='batch_0NrZ2I9E7NMlDkRI2Zm8zglm', completion_window='24h', created_at=1726233395, endpoint='/v1/chat/completions', input_file_id='file-HfMbJ2tKqWAwYvlW3nYtdhIO', object='batch', status='validating', cancelled_at=None, cancelling_at=None, completed_at=None, error_file_id=None, errors=None, expired_at=None, expires_at=1726319795, failed_at=None, finalizing_at=None, in_progress_at=None, metadata={'description': 'nightly eval job - o1-mini'}, output_file_id=None, request_counts=BatchRequestCounts(completed=0, failed=0, total=0))

In [24]:
from openai import OpenAI

client = OpenAI()

client.batches.retrieve("batch_0NrZ2I9E7NMlDkRI2Zm8zglm")

Batch(id='batch_0NrZ2I9E7NMlDkRI2Zm8zglm', completion_window='24h', created_at=1726233395, endpoint='/v1/chat/completions', input_file_id='file-HfMbJ2tKqWAwYvlW3nYtdhIO', object='batch', status='failed', cancelled_at=None, cancelling_at=None, completed_at=None, error_file_id=None, errors=Errors(data=[BatchError(code='model_not_found', line=1, message="The provided model 'o1-mini' is not supported by the Batch API.", param='body.model'), BatchError(code='model_not_found', line=2, message="The provided model 'o1-mini' is not supported by the Batch API.", param='body.model'), BatchError(code='model_not_found', line=3, message="The provided model 'o1-mini' is not supported by the Batch API.", param='body.model'), BatchError(code='model_not_found', line=4, message="The provided model 'o1-mini' is not supported by the Batch API.", param='body.model'), BatchError(code='model_not_found', line=5, message="The provided model 'o1-mini' is not supported by the Batch API.", param='body.model'), Bat

## Run Completion Endpoints

In [9]:
from llm_toolkit.eval_openai import evaluate_model_with_num_shots

loading env vars from: d:\code\projects\logical-reasoning\.env
Adding d:\code\projects\logical-reasoning to sys.path
claude-3-5-sonnet-20240620 datasets/mgtv data/openai_results.csv 16


In [29]:
%%time

model_name ="o1-mini"

evaluate_model_with_num_shots(
    model_name,
    datasets,
    results_path=results_path,
    range_num_shots=[10],
    max_new_tokens=max_new_tokens,
)

loading d:\code\projects\logical-reasoning\llm_toolkit\logical_reasoning_utils.py
Evaluating model: o1-mini
--------------------------------------------------
text: 甄加索是自杀吗
--------------------------------------------------
label: 不是
--------------------------------------------------
answer: nan
--------------------------------------------------
title: 海岸之谜
--------------------------------------------------
puzzle: 在远离城市喧嚣的海边小屋，一天清晨，邻居发现甄加索僵卧在沙滩上，已无生命迹象。现场没有发现任何打斗的迹象。请问甄加索的死因是什么？
--------------------------------------------------
truth: 甄加索是一位热爱自然的画家，他每年都会来到这个海边小屋寻找灵感。在他生命的最后几天，他一直在创作一幅描绘海洋生物的画作。在画即将完成的前一天晚上，他骑着自行车外出，打算在海边观赏夜景。然而，他在沙滩上意外发现了一只搁浅的海豚，为了救助这只海豚，他耗费了极大的体力，最终成功将其送回海中。筋疲力尽的甄加索在沙滩上睡着了，由于他患有严重的心脏病，却未告知旁人，在寒冷的海风中，他的心脏停止了跳动。因此，警方在现场只发现了车轮痕迹和未完成的画作，而没有发现任何他杀的迹象。
*** Evaluating with num_shots: 10
user_prompt: 你是一个情景猜谜游戏的主持人。游戏规则如下：

1. 参与者会得到一个谜面，谜面会描述一个简单又难以理解的事件。
2. 主持人知道谜底，谜底是谜面的答案。
3. 参与者可以询问任何封闭式问题来找寻事件的真相。
4. 对于每个问题，主持人将根据实际情况回答以下五个选项之一：是、不是、不重要、回答正确、问法错误。各回答的判断标准如下：
   - 若谜面和

100%|██████████| 3000/3000 [7:34:45<00:00,  9.10s/it]   

o1-mini/shots-10 metrics: {'accuracy': 0.725, 'incorrect_ids': [3, 9, 12, 17, 18, 21, 23, 25, 28, 29, 31, 32, 33, 34, 37, 38, 43, 54, 55, 59, 60, 61, 64, 65, 67, 71, 75, 78, 81, 82, 83, 88, 97, 102, 104, 105, 106, 108, 110, 116, 117, 124, 125, 127, 128, 131, 137, 139, 149, 150, 153, 155, 160, 161, 163, 164, 171, 179, 188, 190, 192, 193, 198, 200, 207, 222, 224, 226, 228, 229, 231, 235, 237, 238, 240, 243, 245, 248, 250, 251, 252, 255, 259, 260, 263, 264, 271, 273, 284, 286, 289, 290, 292, 293, 295, 299, 303, 304, 305, 322, 323, 328, 330, 333, 334, 335, 342, 344, 349, 350, 351, 356, 357, 360, 362, 364, 368, 369, 370, 374, 377, 389, 395, 396, 397, 414, 421, 429, 430, 431, 449, 450, 453, 454, 456, 457, 458, 461, 463, 464, 465, 466, 469, 472, 477, 481, 482, 483, 485, 486, 487, 489, 490, 492, 494, 495, 501, 502, 503, 506, 507, 508, 509, 510, 511, 516, 517, 519, 520, 530, 531, 534, 536, 540, 544, 560, 566, 568, 571, 579, 581, 582, 585, 589, 591, 592, 594, 596, 600, 601, 609, 612, 613, 614, 6

In [10]:
%%time

model_name ="o1-preview"

evaluate_model_with_num_shots(
    model_name,
    datasets,
    results_path=results_path,
    range_num_shots=[10],
    max_new_tokens=max_new_tokens,
)

Evaluating model: o1-preview
--------------------------------------------------
text: 甄加索是自杀吗
--------------------------------------------------
label: 不是
--------------------------------------------------
answer: nan
--------------------------------------------------
title: 海岸之谜
--------------------------------------------------
puzzle: 在远离城市喧嚣的海边小屋，一天清晨，邻居发现甄加索僵卧在沙滩上，已无生命迹象。现场没有发现任何打斗的迹象。请问甄加索的死因是什么？
--------------------------------------------------
truth: 甄加索是一位热爱自然的画家，他每年都会来到这个海边小屋寻找灵感。在他生命的最后几天，他一直在创作一幅描绘海洋生物的画作。在画即将完成的前一天晚上，他骑着自行车外出，打算在海边观赏夜景。然而，他在沙滩上意外发现了一只搁浅的海豚，为了救助这只海豚，他耗费了极大的体力，最终成功将其送回海中。筋疲力尽的甄加索在沙滩上睡着了，由于他患有严重的心脏病，却未告知旁人，在寒冷的海风中，他的心脏停止了跳动。因此，警方在现场只发现了车轮痕迹和未完成的画作，而没有发现任何他杀的迹象。
*** Evaluating with num_shots: 10
user_prompt: 你是一个情景猜谜游戏的主持人。游戏规则如下：

1. 参与者会得到一个谜面，谜面会描述一个简单又难以理解的事件。
2. 主持人知道谜底，谜底是谜面的答案。
3. 参与者可以询问任何封闭式问题来找寻事件的真相。
4. 对于每个问题，主持人将根据实际情况回答以下五个选项之一：是、不是、不重要、回答正确、问法错误。各回答的判断标准如下：
   - 若谜面和谜底能找到问题的答案，回答：是或者不是
   - 若谜面和谜底不能直接或者间接推断出问题的答案，回答：不重要
   - 若参与者提问不是一个封闭式问题或者问题

100%|██████████| 3000/3000 [19:29:34<00:00, 23.39s/it]    


o1-preview/shots-10 metrics: {'accuracy': 0.749, 'incorrect_ids': [11, 18, 19, 23, 26, 27, 29, 31, 35, 36, 37, 38, 55, 58, 59, 60, 61, 64, 65, 67, 78, 81, 83, 91, 104, 105, 107, 108, 109, 112, 113, 116, 117, 120, 122, 124, 128, 129, 131, 136, 139, 150, 153, 155, 160, 161, 163, 164, 171, 173, 176, 180, 191, 193, 198, 200, 207, 215, 221, 228, 230, 231, 238, 243, 245, 248, 249, 250, 251, 252, 255, 259, 260, 273, 274, 280, 283, 284, 286, 292, 293, 295, 299, 303, 304, 318, 319, 321, 324, 325, 330, 333, 334, 335, 347, 356, 360, 362, 364, 365, 368, 370, 371, 373, 374, 377, 383, 389, 390, 395, 396, 397, 403, 404, 408, 410, 413, 420, 429, 430, 438, 445, 449, 452, 453, 454, 456, 457, 458, 461, 463, 464, 465, 466, 472, 475, 476, 481, 483, 485, 486, 487, 488, 492, 493, 494, 495, 496, 498, 500, 501, 502, 503, 506, 507, 508, 509, 510, 512, 515, 516, 517, 519, 520, 534, 536, 544, 560, 566, 571, 579, 581, 585, 589, 591, 596, 597, 598, 599, 601, 613, 614, 618, 621, 622, 625, 626, 629, 632, 633, 635, 63

In [11]:
%%time

model_name ="o1-mini"

evaluate_model_with_num_shots(
    model_name,
    datasets,
    results_path=results_path,
    range_num_shots=[0],
    max_new_tokens=max_new_tokens,
)

loading d:\code\projects\logical-reasoning\llm_toolkit\logical_reasoning_utils.py
Evaluating model: o1-mini
--------------------------------------------------
text: 甄加索是自杀吗
--------------------------------------------------
label: 不是
--------------------------------------------------
answer: nan
--------------------------------------------------
title: 海岸之谜
--------------------------------------------------
puzzle: 在远离城市喧嚣的海边小屋，一天清晨，邻居发现甄加索僵卧在沙滩上，已无生命迹象。现场没有发现任何打斗的迹象。请问甄加索的死因是什么？
--------------------------------------------------
truth: 甄加索是一位热爱自然的画家，他每年都会来到这个海边小屋寻找灵感。在他生命的最后几天，他一直在创作一幅描绘海洋生物的画作。在画即将完成的前一天晚上，他骑着自行车外出，打算在海边观赏夜景。然而，他在沙滩上意外发现了一只搁浅的海豚，为了救助这只海豚，他耗费了极大的体力，最终成功将其送回海中。筋疲力尽的甄加索在沙滩上睡着了，由于他患有严重的心脏病，却未告知旁人，在寒冷的海风中，他的心脏停止了跳动。因此，警方在现场只发现了车轮痕迹和未完成的画作，而没有发现任何他杀的迹象。
*** Evaluating with num_shots: 0
user_prompt: 你是一个情景猜谜游戏的主持人。游戏规则如下：

1. 参与者会得到一个谜面，谜面会描述一个简单又难以理解的事件。
2. 主持人知道谜底，谜底是谜面的答案。
3. 参与者可以询问任何封闭式问题来找寻事件的真相。
4. 对于每个问题，主持人将根据实际情况回答以下五个选项之一：是、不是、不重要、回答正确、问法错误。各回答的判断标准如下：
   - 若谜面和谜

100%|██████████| 3000/3000 [7:01:16<00:00,  8.43s/it]   


o1-mini/shots-00 metrics: {'accuracy': 0.7083333333333334, 'incorrect_ids': [11, 12, 15, 16, 18, 21, 23, 24, 25, 28, 34, 43, 47, 54, 55, 59, 62, 63, 65, 78, 80, 81, 83, 88, 97, 104, 105, 106, 109, 112, 113, 115, 116, 117, 120, 121, 125, 126, 128, 129, 131, 135, 141, 143, 149, 150, 153, 155, 161, 163, 164, 172, 176, 179, 180, 189, 198, 200, 215, 224, 225, 228, 230, 232, 234, 235, 236, 238, 242, 243, 245, 248, 250, 251, 252, 253, 255, 259, 260, 264, 271, 273, 283, 284, 286, 287, 292, 293, 295, 299, 301, 303, 304, 308, 311, 313, 323, 325, 330, 331, 333, 334, 335, 351, 353, 354, 355, 356, 358, 359, 360, 362, 364, 365, 368, 369, 370, 371, 373, 374, 377, 383, 384, 395, 396, 406, 409, 414, 417, 421, 429, 430, 438, 440, 447, 449, 453, 454, 455, 457, 458, 461, 462, 463, 464, 465, 472, 475, 476, 481, 485, 487, 488, 490, 492, 493, 494, 495, 497, 498, 500, 501, 502, 503, 506, 507, 508, 509, 516, 517, 519, 520, 533, 536, 538, 539, 540, 553, 560, 566, 568, 571, 579, 581, 582, 589, 591, 592, 594, 596

In [14]:
%%time

model_name ="o1-preview"

evaluate_model_with_num_shots(
    model_name,
    datasets,
    results_path=results_path,
    range_num_shots=[0],
    max_new_tokens=max_new_tokens,
)

Evaluating model: o1-preview
--------------------------------------------------
text: 甄加索是自杀吗
--------------------------------------------------
label: 不是
--------------------------------------------------
answer: nan
--------------------------------------------------
title: 海岸之谜
--------------------------------------------------
puzzle: 在远离城市喧嚣的海边小屋，一天清晨，邻居发现甄加索僵卧在沙滩上，已无生命迹象。现场没有发现任何打斗的迹象。请问甄加索的死因是什么？
--------------------------------------------------
truth: 甄加索是一位热爱自然的画家，他每年都会来到这个海边小屋寻找灵感。在他生命的最后几天，他一直在创作一幅描绘海洋生物的画作。在画即将完成的前一天晚上，他骑着自行车外出，打算在海边观赏夜景。然而，他在沙滩上意外发现了一只搁浅的海豚，为了救助这只海豚，他耗费了极大的体力，最终成功将其送回海中。筋疲力尽的甄加索在沙滩上睡着了，由于他患有严重的心脏病，却未告知旁人，在寒冷的海风中，他的心脏停止了跳动。因此，警方在现场只发现了车轮痕迹和未完成的画作，而没有发现任何他杀的迹象。
*** Evaluating with num_shots: 0
user_prompt: 你是一个情景猜谜游戏的主持人。游戏规则如下：

1. 参与者会得到一个谜面，谜面会描述一个简单又难以理解的事件。
2. 主持人知道谜底，谜底是谜面的答案。
3. 参与者可以询问任何封闭式问题来找寻事件的真相。
4. 对于每个问题，主持人将根据实际情况回答以下五个选项之一：是、不是、不重要、回答正确、问法错误。各回答的判断标准如下：
   - 若谜面和谜底能找到问题的答案，回答：是或者不是
   - 若谜面和谜底不能直接或者间接推断出问题的答案，回答：不重要
   - 若参与者提问不是一个封闭式问题或者问题难

100%|██████████| 3000/3000 [9:41:42<00:00, 11.63s/it]  


o1-preview/shots-00 metrics: {'accuracy': 0.721, 'incorrect_ids': [6, 8, 10, 11, 12, 16, 17, 18, 19, 23, 25, 26, 29, 33, 34, 35, 36, 37, 38, 43, 48, 52, 55, 58, 59, 60, 62, 65, 67, 78, 81, 82, 83, 91, 93, 97, 101, 104, 105, 107, 108, 109, 113, 114, 117, 120, 122, 124, 128, 129, 131, 136, 138, 141, 150, 153, 155, 160, 161, 163, 164, 173, 191, 193, 194, 195, 198, 199, 200, 201, 207, 221, 222, 224, 227, 230, 231, 232, 234, 235, 236, 238, 239, 243, 245, 249, 250, 251, 255, 257, 259, 260, 262, 263, 267, 270, 271, 276, 281, 282, 283, 284, 286, 290, 294, 299, 303, 304, 309, 310, 311, 313, 314, 318, 319, 321, 324, 330, 334, 335, 342, 356, 360, 362, 364, 368, 370, 371, 372, 373, 374, 377, 383, 384, 396, 397, 409, 410, 414, 416, 426, 429, 430, 447, 449, 453, 454, 457, 458, 461, 463, 464, 465, 466, 472, 474, 475, 476, 478, 479, 480, 481, 485, 486, 487, 488, 489, 490, 491, 492, 493, 494, 495, 496, 497, 498, 499, 500, 501, 503, 505, 506, 508, 510, 511, 512, 514, 515, 516, 517, 518, 519, 520, 533, 5

In [15]:
%%time

model_name ="o1-mini"

evaluate_model_with_num_shots(
    model_name,
    datasets,
    results_path=results_path,
    range_num_shots=[5, 20],
    max_new_tokens=max_new_tokens,
)

Evaluating model: o1-mini
--------------------------------------------------
text: 甄加索是自杀吗
--------------------------------------------------
label: 不是
--------------------------------------------------
answer: nan
--------------------------------------------------
title: 海岸之谜
--------------------------------------------------
puzzle: 在远离城市喧嚣的海边小屋，一天清晨，邻居发现甄加索僵卧在沙滩上，已无生命迹象。现场没有发现任何打斗的迹象。请问甄加索的死因是什么？
--------------------------------------------------
truth: 甄加索是一位热爱自然的画家，他每年都会来到这个海边小屋寻找灵感。在他生命的最后几天，他一直在创作一幅描绘海洋生物的画作。在画即将完成的前一天晚上，他骑着自行车外出，打算在海边观赏夜景。然而，他在沙滩上意外发现了一只搁浅的海豚，为了救助这只海豚，他耗费了极大的体力，最终成功将其送回海中。筋疲力尽的甄加索在沙滩上睡着了，由于他患有严重的心脏病，却未告知旁人，在寒冷的海风中，他的心脏停止了跳动。因此，警方在现场只发现了车轮痕迹和未完成的画作，而没有发现任何他杀的迹象。
*** Evaluating with num_shots: 5
user_prompt: 你是一个情景猜谜游戏的主持人。游戏规则如下：

1. 参与者会得到一个谜面，谜面会描述一个简单又难以理解的事件。
2. 主持人知道谜底，谜底是谜面的答案。
3. 参与者可以询问任何封闭式问题来找寻事件的真相。
4. 对于每个问题，主持人将根据实际情况回答以下五个选项之一：是、不是、不重要、回答正确、问法错误。各回答的判断标准如下：
   - 若谜面和谜底能找到问题的答案，回答：是或者不是
   - 若谜面和谜底不能直接或者间接推断出问题的答案，回答：不重要
   - 若参与者提问不是一个封闭式问题或者问题难以理解

100%|██████████| 3000/3000 [4:48:29<00:00,  5.77s/it]  


o1-mini/shots-05 metrics: {'accuracy': 0.724, 'incorrect_ids': [5, 9, 16, 18, 23, 24, 25, 28, 29, 30, 31, 33, 34, 37, 38, 54, 55, 58, 59, 61, 65, 67, 78, 80, 81, 82, 84, 88, 91, 104, 105, 107, 109, 110, 112, 113, 117, 120, 121, 124, 128, 129, 136, 137, 139, 143, 144, 150, 160, 161, 163, 164, 170, 171, 173, 179, 190, 191, 198, 200, 220, 222, 223, 224, 228, 229, 230, 231, 235, 236, 238, 243, 245, 248, 250, 251, 252, 253, 255, 259, 260, 263, 265, 271, 273, 276, 283, 284, 290, 292, 295, 299, 303, 304, 309, 318, 321, 322, 323, 330, 331, 333, 334, 335, 343, 350, 355, 356, 360, 363, 368, 370, 371, 373, 374, 377, 379, 383, 389, 394, 395, 396, 397, 409, 410, 416, 421, 425, 429, 430, 445, 447, 449, 454, 456, 457, 458, 461, 464, 466, 467, 475, 477, 478, 479, 480, 481, 483, 484, 488, 490, 492, 493, 494, 495, 498, 501, 502, 503, 504, 506, 507, 508, 509, 510, 511, 512, 517, 519, 520, 531, 536, 540, 544, 553, 560, 566, 571, 579, 581, 585, 589, 591, 592, 594, 596, 597, 599, 601, 612, 613, 614, 621, 62

100%|██████████| 3000/3000 [5:10:18<00:00,  6.21s/it]   

o1-mini/shots-20 metrics: {'accuracy': 0.7343333333333333, 'incorrect_ids': [12, 13, 16, 18, 21, 25, 29, 31, 37, 54, 55, 59, 60, 61, 62, 63, 65, 67, 78, 80, 81, 82, 83, 84, 91, 93, 97, 103, 104, 105, 106, 116, 117, 120, 121, 122, 126, 128, 129, 131, 137, 138, 143, 150, 155, 160, 161, 163, 164, 171, 173, 174, 179, 188, 190, 194, 198, 199, 200, 222, 224, 228, 229, 231, 235, 236, 238, 243, 245, 250, 251, 257, 259, 260, 263, 264, 271, 272, 273, 286, 289, 290, 293, 295, 299, 303, 304, 315, 318, 321, 323, 328, 330, 333, 334, 335, 349, 351, 354, 355, 356, 359, 360, 362, 368, 369, 370, 371, 373, 374, 376, 383, 386, 389, 395, 396, 397, 409, 410, 414, 416, 421, 429, 430, 438, 447, 449, 454, 457, 461, 462, 463, 464, 465, 466, 471, 472, 473, 474, 475, 481, 488, 492, 493, 494, 495, 501, 502, 503, 506, 507, 508, 509, 510, 511, 515, 516, 517, 519, 520, 536, 544, 556, 560, 566, 570, 571, 574, 579, 581, 589, 591, 601, 610, 612, 613, 614, 621, 625, 628, 629, 632, 636, 643, 644, 647, 650, 663, 666, 671, 

In [16]:
%%time

model_name ="o1-preview"

evaluate_model_with_num_shots(
    model_name,
    datasets,
    results_path=results_path,
    range_num_shots=[5, 20],
    max_new_tokens=max_new_tokens,
)

Evaluating model: o1-preview
--------------------------------------------------
text: 甄加索是自杀吗
--------------------------------------------------
label: 不是
--------------------------------------------------
answer: nan
--------------------------------------------------
title: 海岸之谜
--------------------------------------------------
puzzle: 在远离城市喧嚣的海边小屋，一天清晨，邻居发现甄加索僵卧在沙滩上，已无生命迹象。现场没有发现任何打斗的迹象。请问甄加索的死因是什么？
--------------------------------------------------
truth: 甄加索是一位热爱自然的画家，他每年都会来到这个海边小屋寻找灵感。在他生命的最后几天，他一直在创作一幅描绘海洋生物的画作。在画即将完成的前一天晚上，他骑着自行车外出，打算在海边观赏夜景。然而，他在沙滩上意外发现了一只搁浅的海豚，为了救助这只海豚，他耗费了极大的体力，最终成功将其送回海中。筋疲力尽的甄加索在沙滩上睡着了，由于他患有严重的心脏病，却未告知旁人，在寒冷的海风中，他的心脏停止了跳动。因此，警方在现场只发现了车轮痕迹和未完成的画作，而没有发现任何他杀的迹象。
*** Evaluating with num_shots: 5
user_prompt: 你是一个情景猜谜游戏的主持人。游戏规则如下：

1. 参与者会得到一个谜面，谜面会描述一个简单又难以理解的事件。
2. 主持人知道谜底，谜底是谜面的答案。
3. 参与者可以询问任何封闭式问题来找寻事件的真相。
4. 对于每个问题，主持人将根据实际情况回答以下五个选项之一：是、不是、不重要、回答正确、问法错误。各回答的判断标准如下：
   - 若谜面和谜底能找到问题的答案，回答：是或者不是
   - 若谜面和谜底不能直接或者间接推断出问题的答案，回答：不重要
   - 若参与者提问不是一个封闭式问题或者问题难

100%|██████████| 3000/3000 [10:45:02<00:00, 12.90s/it] 


o1-preview/shots-05 metrics: {'accuracy': 0.7313333333333333, 'incorrect_ids': [6, 10, 11, 17, 18, 19, 21, 25, 26, 27, 28, 29, 31, 34, 35, 38, 43, 50, 52, 55, 58, 59, 60, 61, 62, 64, 65, 78, 81, 91, 94, 97, 104, 105, 108, 109, 110, 112, 113, 114, 117, 120, 121, 122, 124, 125, 128, 129, 131, 136, 138, 139, 142, 150, 155, 160, 161, 163, 164, 171, 172, 173, 179, 191, 193, 194, 198, 200, 201, 207, 215, 220, 224, 226, 228, 230, 231, 232, 234, 235, 236, 238, 240, 243, 245, 248, 249, 250, 251, 254, 255, 259, 260, 262, 267, 269, 271, 273, 280, 282, 283, 284, 292, 294, 295, 299, 303, 304, 311, 312, 318, 319, 323, 324, 325, 330, 334, 335, 356, 360, 362, 364, 368, 370, 371, 373, 374, 375, 377, 383, 384, 389, 390, 395, 397, 398, 400, 410, 416, 419, 421, 423, 429, 430, 449, 453, 454, 457, 458, 461, 462, 464, 465, 466, 472, 474, 475, 476, 478, 481, 482, 483, 485, 486, 487, 488, 489, 490, 492, 493, 495, 496, 500, 501, 502, 503, 506, 507, 508, 510, 511, 516, 517, 518, 519, 520, 536, 539, 540, 544, 560

100%|██████████| 3000/3000 [11:13:38<00:00, 13.47s/it]  


o1-preview/shots-20 metrics: {'accuracy': 0.7443333333333333, 'incorrect_ids': [6, 10, 11, 17, 18, 21, 23, 24, 25, 27, 29, 31, 36, 37, 43, 55, 58, 59, 60, 61, 64, 65, 67, 78, 81, 83, 91, 94, 97, 104, 105, 107, 112, 113, 117, 119, 120, 122, 124, 125, 128, 129, 131, 136, 139, 150, 155, 161, 163, 164, 171, 173, 180, 191, 194, 198, 199, 201, 222, 224, 225, 228, 229, 230, 231, 236, 237, 238, 239, 240, 243, 245, 250, 251, 254, 255, 259, 260, 271, 273, 281, 283, 284, 286, 292, 293, 295, 299, 303, 304, 308, 310, 311, 318, 319, 321, 324, 326, 330, 332, 333, 334, 335, 342, 356, 360, 364, 365, 368, 370, 371, 373, 374, 377, 383, 384, 389, 396, 397, 410, 413, 419, 429, 430, 445, 447, 449, 453, 454, 456, 457, 458, 461, 462, 465, 466, 472, 474, 475, 476, 479, 481, 485, 486, 488, 490, 492, 493, 494, 495, 496, 498, 500, 501, 502, 503, 506, 507, 508, 509, 510, 511, 515, 516, 517, 518, 519, 520, 534, 536, 540, 543, 544, 560, 566, 571, 572, 579, 581, 582, 589, 591, 594, 595, 596, 598, 599, 601, 614, 618, 

In [17]:
%%time

for model_name in ["o1-preview", "o1-mini"]:
    evaluate_model_with_num_shots(
        model_name,
        datasets,
        results_path=results_path,
        range_num_shots=[50, 40, 30],
        max_new_tokens=max_new_tokens,
    )

Evaluating model: o1-preview
--------------------------------------------------
text: 甄加索是自杀吗
--------------------------------------------------
label: 不是
--------------------------------------------------
answer: nan
--------------------------------------------------
title: 海岸之谜
--------------------------------------------------
puzzle: 在远离城市喧嚣的海边小屋，一天清晨，邻居发现甄加索僵卧在沙滩上，已无生命迹象。现场没有发现任何打斗的迹象。请问甄加索的死因是什么？
--------------------------------------------------
truth: 甄加索是一位热爱自然的画家，他每年都会来到这个海边小屋寻找灵感。在他生命的最后几天，他一直在创作一幅描绘海洋生物的画作。在画即将完成的前一天晚上，他骑着自行车外出，打算在海边观赏夜景。然而，他在沙滩上意外发现了一只搁浅的海豚，为了救助这只海豚，他耗费了极大的体力，最终成功将其送回海中。筋疲力尽的甄加索在沙滩上睡着了，由于他患有严重的心脏病，却未告知旁人，在寒冷的海风中，他的心脏停止了跳动。因此，警方在现场只发现了车轮痕迹和未完成的画作，而没有发现任何他杀的迹象。
*** Evaluating with num_shots: 50
user_prompt: 你是一个情景猜谜游戏的主持人。游戏规则如下：

1. 参与者会得到一个谜面，谜面会描述一个简单又难以理解的事件。
2. 主持人知道谜底，谜底是谜面的答案。
3. 参与者可以询问任何封闭式问题来找寻事件的真相。
4. 对于每个问题，主持人将根据实际情况回答以下五个选项之一：是、不是、不重要、回答正确、问法错误。各回答的判断标准如下：
   - 若谜面和谜底能找到问题的答案，回答：是或者不是
   - 若谜面和谜底不能直接或者间接推断出问题的答案，回答：不重要
   - 若参与者提问不是一个封闭式问题或者问题

100%|██████████| 3000/3000 [11:08:31<00:00, 13.37s/it]  


o1-preview/shots-50 metrics: {'accuracy': 0.7546666666666667, 'incorrect_ids': [6, 10, 11, 18, 24, 25, 26, 29, 31, 51, 55, 58, 59, 60, 64, 65, 67, 78, 81, 83, 84, 88, 91, 94, 97, 104, 105, 107, 108, 112, 113, 114, 117, 120, 121, 122, 124, 125, 128, 129, 131, 150, 155, 160, 161, 163, 164, 171, 172, 173, 179, 180, 193, 194, 198, 200, 201, 207, 222, 225, 228, 230, 231, 236, 237, 238, 243, 245, 249, 250, 251, 252, 255, 259, 260, 262, 263, 269, 271, 280, 283, 284, 286, 290, 292, 294, 295, 299, 303, 304, 308, 310, 311, 314, 318, 319, 326, 330, 333, 334, 335, 356, 357, 360, 362, 364, 368, 370, 371, 372, 373, 374, 375, 377, 383, 384, 396, 399, 410, 414, 415, 417, 421, 425, 430, 447, 449, 453, 454, 456, 457, 458, 461, 462, 464, 465, 472, 474, 475, 476, 480, 481, 485, 486, 487, 488, 490, 492, 494, 495, 496, 497, 498, 500, 502, 503, 506, 507, 508, 509, 510, 511, 516, 517, 519, 520, 536, 540, 544, 560, 566, 571, 572, 573, 579, 581, 589, 591, 596, 597, 598, 601, 613, 614, 621, 622, 625, 628, 629, 6

100%|██████████| 3000/3000 [11:33:17<00:00, 13.87s/it]  


o1-preview/shots-40 metrics: {'accuracy': 0.7506666666666667, 'incorrect_ids': [6, 11, 17, 18, 19, 23, 25, 26, 27, 29, 31, 37, 43, 47, 55, 58, 59, 60, 61, 65, 78, 81, 83, 91, 93, 94, 97, 104, 105, 108, 109, 112, 117, 118, 120, 121, 124, 125, 128, 129, 131, 136, 150, 155, 160, 161, 164, 171, 173, 179, 189, 193, 194, 198, 200, 201, 207, 221, 222, 224, 226, 228, 229, 230, 231, 236, 238, 240, 243, 245, 249, 250, 251, 252, 255, 259, 260, 271, 283, 284, 286, 292, 295, 299, 303, 304, 318, 319, 324, 326, 330, 333, 334, 335, 342, 356, 360, 362, 364, 368, 369, 370, 371, 372, 373, 374, 377, 383, 384, 389, 397, 400, 410, 429, 430, 449, 452, 453, 454, 456, 457, 458, 461, 462, 463, 464, 465, 472, 473, 475, 476, 478, 479, 481, 482, 485, 486, 487, 488, 490, 492, 493, 494, 495, 496, 498, 499, 500, 501, 502, 503, 506, 507, 508, 509, 510, 511, 516, 517, 519, 520, 536, 543, 560, 566, 571, 572, 579, 581, 589, 591, 596, 597, 599, 601, 612, 613, 614, 618, 621, 622, 623, 626, 628, 629, 632, 633, 635, 636, 644

100%|██████████| 3000/3000 [11:48:09<00:00, 14.16s/it]  


o1-preview/shots-30 metrics: {'accuracy': 0.7473333333333333, 'incorrect_ids': [10, 11, 13, 17, 18, 23, 25, 27, 29, 31, 35, 52, 55, 58, 59, 60, 64, 65, 67, 78, 81, 82, 83, 91, 94, 97, 101, 104, 105, 107, 108, 110, 112, 113, 115, 116, 117, 120, 122, 124, 128, 129, 131, 139, 143, 150, 153, 155, 160, 161, 163, 164, 172, 173, 179, 180, 191, 193, 198, 201, 207, 222, 224, 228, 230, 231, 234, 235, 236, 238, 239, 240, 243, 245, 248, 249, 250, 251, 252, 253, 255, 259, 260, 262, 267, 271, 276, 280, 282, 284, 290, 292, 293, 294, 295, 299, 303, 304, 308, 314, 318, 319, 324, 326, 330, 333, 334, 335, 355, 356, 358, 360, 362, 364, 368, 370, 371, 372, 373, 374, 375, 377, 383, 384, 389, 396, 397, 402, 410, 419, 429, 430, 447, 449, 452, 453, 454, 456, 457, 458, 461, 463, 464, 465, 466, 472, 475, 476, 481, 485, 486, 487, 488, 492, 494, 495, 496, 498, 500, 501, 502, 503, 506, 507, 508, 509, 510, 511, 515, 516, 517, 519, 520, 531, 536, 540, 543, 544, 560, 566, 570, 571, 579, 580, 581, 582, 589, 591, 594, 5

 21%|██        | 636/3000 [1:41:55<8:08:34, 12.40s/it] 